In [6]:
from transformers import AutoModelWithLMHead, AutoTokenizer, AutoModel
import torch
from torch import nn
import json
import numpy as np
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import train_test_split,StratifiedShuffleSplit
from torch.utils.data import DataLoader,TensorDataset
import pickle
from sklearn.metrics import confusion_matrix,classification_report

In [7]:
with open('pruned_json.json') as json_file:
    data = json.load(json_file)
len(data)

242

In [8]:
tokenizer = AutoTokenizer.from_pretrained("emilyalsentzer/Bio_ClinicalBERT")
model = AutoModel.from_pretrained("emilyalsentzer/Bio_ClinicalBERT")

Some weights of the model checkpoint at emilyalsentzer/Bio_ClinicalBERT were not used when initializing BertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


# Using Clinical Bert as word embedding

## Get Report Embedding by using Mean of Sentences Embedding 

In [11]:
def get_cls_tensor(sents, tokenizer, model):
    tokenized_sents = tokenizer(sents,padding="max_length", truncation=True, return_tensors="pt",max_length=512)["input_ids"]
    tokenized_sents.cuda()
    model.eval()
    model.cuda()
    last_hidden_state = model(tokenized_sents.cuda()).last_hidden_state
    cls_state = last_hidden_state[:,0,:]
    return torch.mean(cls_state,axis=0)

In [12]:
label = []
inputs = []
with torch.no_grad():
    for k,v in data.items():
        label.append(v["isRejection"])
        inputs.append(get_cls_tensor(v["pruned_report"],tokenizer, model))

# with open('inputs.pkl', 'rb') as f:
#     inputs = pickle.load(f)

# label = []
# inputs = []
# with torch.no_grad():
#     for k,v in data.items():
#         label.append(v["isRejection"])
#         inputs.append(" ".join(v["pruned_report"]))

In [21]:
train_features, test_features, train_labels, test_labels = train_test_split(
    inputs, label,random_state = 1,stratify=label,test_size=0.2)

# train_features = tokenizer(train_features,padding="max_length", truncation=True, 
#                             return_tensors="pt",max_length=512)
# test_features = tokenizer(test_features,padding="max_length", truncation=True, 
#                             return_tensors="pt",max_length=512)

### Try Logistic Regression

In [22]:
lr_clf = LogisticRegression(max_iter = 500)
train_features = [i.cpu().numpy() for i in train_features]
train_features
lr_clf.fit(train_features, train_labels)


LogisticRegression(max_iter=500)

In [24]:
test_features = [i.cpu().numpy() for i in test_features]
lr_clf.score(test_features, test_labels)

0.7755102040816326

In [25]:
y_pred = lr_clf.predict(test_features)

In [26]:
confusion_matrix(test_labels,y_pred)

array([[35,  1],
       [10,  3]], dtype=int64)

In [27]:
print(classification_report(test_labels,y_pred))

              precision    recall  f1-score   support

           0       0.78      0.97      0.86        36
           1       0.75      0.23      0.35        13

    accuracy                           0.78        49
   macro avg       0.76      0.60      0.61        49
weighted avg       0.77      0.78      0.73        49



### Try NN

In [9]:
class Net(torch.nn.Module):
    def __init__(self,n_input,n_hidden,n_output):
        super(Net,self).__init__()
        self.hidden = torch.nn.Linear(n_input,n_hidden)
        self.predict = torch.nn.Linear(n_hidden,n_output)

    def forward(self, input):
        out = self.hidden(input)
        out = torch.sigmoid(out)
        out = self.predict(out)
        return out
model = Net(768,2000,2).cuda()
print(model)

Net(
  (hidden): Linear(in_features=768, out_features=2000, bias=True)
  (predict): Linear(in_features=2000, out_features=2, bias=True)
)


In [10]:
model = torch.load("bert_dense_model.pt").cuda()

In [11]:
EPOCH = 3000
BATCH_SIZE = 8
LR = 0.001

train_data = TensorDataset(torch.tensor(train_features),torch.tensor(train_labels))
train_loader = DataLoader(train_data,batch_size=BATCH_SIZE,shuffle=True)
optimizer = torch.optim.SGD(model.parameters(), lr=LR)
loss_func = torch.nn.CrossEntropyLoss().cuda()

NameError: name 'train_features' is not defined

In [14]:


model.train()
for e in range(EPOCH):
  for i, (x_train, y_train) in enumerate(train_loader):
    
#         if e % 1000 == 0 and e:
#             for g in optimizer.param_groups:
#                 g['lr'] /= 10
        #x_train = x_train.view(-1, 1, 32, 32)  
        x_train, y_train = x_train.cuda(), y_train.cuda()

        output = model(x_train)

        loss = loss_func(output, y_train)      
        optimizer.zero_grad()               
        loss.backward()                     
        optimizer.step()

        print("epoch: {} step: {}/{} loss: {}".format(e,i*BATCH_SIZE,len(train_loader)*BATCH_SIZE,loss.item()))

epoch: 0 step: 0/200 loss: 0.7311692237854004
epoch: 0 step: 8/200 loss: 0.6760748624801636
epoch: 0 step: 16/200 loss: 0.608641505241394
epoch: 0 step: 24/200 loss: 0.5189143419265747
epoch: 0 step: 32/200 loss: 0.5697355270385742
epoch: 0 step: 40/200 loss: 0.6765278577804565
epoch: 0 step: 48/200 loss: 0.6701498031616211
epoch: 0 step: 56/200 loss: 0.5759927034378052
epoch: 0 step: 64/200 loss: 0.771711528301239
epoch: 0 step: 72/200 loss: 0.5870347619056702
epoch: 0 step: 80/200 loss: 0.6661078333854675
epoch: 0 step: 88/200 loss: 0.49777957797050476
epoch: 0 step: 96/200 loss: 0.788621723651886
epoch: 0 step: 104/200 loss: 0.5801013112068176
epoch: 0 step: 112/200 loss: 0.7633630633354187
epoch: 0 step: 120/200 loss: 0.44629767537117004
epoch: 0 step: 128/200 loss: 0.5642684102058411
epoch: 0 step: 136/200 loss: 0.4414702355861664
epoch: 0 step: 144/200 loss: 0.7043119668960571
epoch: 0 step: 152/200 loss: 0.5627415776252747
epoch: 0 step: 160/200 loss: 0.5629010200500488
epoch: 0

In [23]:
correct = 0
test_data = TensorDataset(torch.tensor(test_features),torch.tensor(test_labels))
test_loader = DataLoader(test_data,
                          batch_size=BATCH_SIZE,shuffle=False)
loss = []
model.eval()
pred_lst = []
for x_test, y_test in test_loader:
    x_test, y_test = x_test.cuda(), y_test.cuda()
    output = model(x_test)
    loss.append(loss_func(output, y_test).item())  

    pred = output.data.max(1, keepdim=True)[1]
    pred_lst.append(pred)
    correct += pred.eq(y_test.data.view_as(pred)).cuda().sum()
    #print(pred.eq(y_test.data.view_as(pred)).cuda(),pred.eq(y_test.data.view_as(pred)).cuda().sum())
print(correct)
print('Loss on test data is:{:.5f}'.format(np.mean(np.array(loss))))
print('Accuracy on test data is:{:.5f}%'.format(100.*correct / len(test_loader.dataset)))

/project/6049037/ytc1997/renal_nlp/lib/python3.7/site-packages/ipykernel_launcher.py:2: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  


tensor(43, device='cuda:0')
Loss on test data is:0.56360
Accuracy on test data is:87.75510%


In [24]:
pred_lst = [x.tolist() for x in pred_lst]
pred_lst = sum(sum(pred_lst, []),[])
confusion_matrix(test_labels,pred_lst)

array([[33,  3],
       [ 3, 10]])

In [25]:
print(classification_report(test_labels,pred_lst))

              precision    recall  f1-score   support

           0       0.92      0.92      0.92        36
           1       0.77      0.77      0.77        13

    accuracy                           0.88        49
   macro avg       0.84      0.84      0.84        49
weighted avg       0.88      0.88      0.88        49



In [18]:
# torch.save(model, "bert_dense_model.pt")

In [ ]:
label_inf = []
inputs_inf = []
c = 0
with torch.no_grad():
    for k,v in data.items():
        if v["diag"] != "":
            try:
                label_inf.append(v["isRejection"])
#                 inputs_inf.append(get_cls_tensor(v["diag"],tokenizer, model))
            except e:
                print(e)
                
with open('inputs_inf.pkl', 'rb') as f:
    inputs_inf = pickle.load(f)

In [35]:
correct = 0
test_data = TensorDataset(train_features,torch.tensor(train_labels))
test_loader = DataLoader(test_data,
                          batch_size=BATCH_SIZE,shuffle=False)
loss = []
model.eval()
pred_lst = []
for x_test, y_test in test_loader:
    x_test, y_test = x_test.cuda(), y_test.cuda()
    output = model(x_test)

    pred = output.data.max(1, keepdim=True)[1]
    pred_lst.append(pred)
    correct += pred.eq(y_test.data.view_as(pred)).cuda().sum()
    #print(pred.eq(y_test.data.view_as(pred)).cuda(),pred.eq(y_test.data.view_as(pred)).cuda().sum())
print(correct)
print('Loss on test data is:{:.5f}'.format(np.mean(np.array(loss))))
print('Accuracy on test data is:{:.5f}%'.format(100.*correct / len(test_loader.dataset)))

tensor(141, device='cuda:0')
Loss on test data is:nan
Accuracy on test data is:73.05699%


/project/6049037/ytc1997/renal_nlp/lib/python3.7/site-packages/numpy/core/fromnumeric.py:3441: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/project/6049037/ytc1997/renal_nlp/lib/python3.7/site-packages/numpy/core/_methods.py:189: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


In [36]:
pred_lst = [x.tolist() for x in pred_lst]
pred_lst = sum(sum(pred_lst, []),[])
confusion_matrix(train_labels,pred_lst)

array([[121,  22],
       [ 30,  20]])

In [37]:
print(classification_report(train_labels,pred_lst))

              precision    recall  f1-score   support

           0       0.80      0.85      0.82       143
           1       0.48      0.40      0.43        50

    accuracy                           0.73       193
   macro avg       0.64      0.62      0.63       193
weighted avg       0.72      0.73      0.72       193



### Try NN

In [9]:
class Net(torch.nn.Module):
    def __init__(self,n_input,n_hidden,n_output):
        super(Net,self).__init__()
        self.hidden = torch.nn.Linear(n_input,n_hidden)
        self.predict = torch.nn.Linear(n_hidden,n_output)

    def forward(self, input):
        out = self.hidden(input)
        out = torch.sigmoid(out)
        out = self.predict(out)
        return out
model = Net(768,2000,2).cuda()
print(model)

Net(
  (hidden): Linear(in_features=768, out_features=2000, bias=True)
  (predict): Linear(in_features=2000, out_features=2, bias=True)
)


In [10]:
model = torch.load("bert_dense_model.pt").cuda()

In [11]:
EPOCH = 3000
BATCH_SIZE = 8
LR = 0.001

train_data = TensorDataset(torch.tensor(train_features),torch.tensor(train_labels))
train_loader = DataLoader(train_data,batch_size=BATCH_SIZE,shuffle=True)
optimizer = torch.optim.SGD(model.parameters(), lr=LR)
loss_func = torch.nn.CrossEntropyLoss().cuda()

NameError: name 'train_features' is not defined

In [14]:


model.train()
for e in range(EPOCH):
  for i, (x_train, y_train) in enumerate(train_loader):
    
#         if e % 1000 == 0 and e:
#             for g in optimizer.param_groups:
#                 g['lr'] /= 10
        #x_train = x_train.view(-1, 1, 32, 32)  
        x_train, y_train = x_train.cuda(), y_train.cuda()

        output = model(x_train)

        loss = loss_func(output, y_train)      
        optimizer.zero_grad()               
        loss.backward()                     
        optimizer.step()

        print("epoch: {} step: {}/{} loss: {}".format(e,i*BATCH_SIZE,len(train_loader)*BATCH_SIZE,loss.item()))

epoch: 0 step: 0/200 loss: 0.7311692237854004
epoch: 0 step: 8/200 loss: 0.6760748624801636
epoch: 0 step: 16/200 loss: 0.608641505241394
epoch: 0 step: 24/200 loss: 0.5189143419265747
epoch: 0 step: 32/200 loss: 0.5697355270385742
epoch: 0 step: 40/200 loss: 0.6765278577804565
epoch: 0 step: 48/200 loss: 0.6701498031616211
epoch: 0 step: 56/200 loss: 0.5759927034378052
epoch: 0 step: 64/200 loss: 0.771711528301239
epoch: 0 step: 72/200 loss: 0.5870347619056702
epoch: 0 step: 80/200 loss: 0.6661078333854675
epoch: 0 step: 88/200 loss: 0.49777957797050476
epoch: 0 step: 96/200 loss: 0.788621723651886
epoch: 0 step: 104/200 loss: 0.5801013112068176
epoch: 0 step: 112/200 loss: 0.7633630633354187
epoch: 0 step: 120/200 loss: 0.44629767537117004
epoch: 0 step: 128/200 loss: 0.5642684102058411
epoch: 0 step: 136/200 loss: 0.4414702355861664
epoch: 0 step: 144/200 loss: 0.7043119668960571
epoch: 0 step: 152/200 loss: 0.5627415776252747
epoch: 0 step: 160/200 loss: 0.5629010200500488
epoch: 0

In [23]:
correct = 0
test_data = TensorDataset(torch.tensor(test_features),torch.tensor(test_labels))
test_loader = DataLoader(test_data,
                          batch_size=BATCH_SIZE,shuffle=False)
loss = []
model.eval()
pred_lst = []
for x_test, y_test in test_loader:
    x_test, y_test = x_test.cuda(), y_test.cuda()
    output = model(x_test)
    loss.append(loss_func(output, y_test).item())  

    pred = output.data.max(1, keepdim=True)[1]
    pred_lst.append(pred)
    correct += pred.eq(y_test.data.view_as(pred)).cuda().sum()
    #print(pred.eq(y_test.data.view_as(pred)).cuda(),pred.eq(y_test.data.view_as(pred)).cuda().sum())
print(correct)
print('Loss on test data is:{:.5f}'.format(np.mean(np.array(loss))))
print('Accuracy on test data is:{:.5f}%'.format(100.*correct / len(test_loader.dataset)))

/project/6049037/ytc1997/renal_nlp/lib/python3.7/site-packages/ipykernel_launcher.py:2: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  


tensor(43, device='cuda:0')
Loss on test data is:0.56360
Accuracy on test data is:87.75510%


In [24]:
pred_lst = [x.tolist() for x in pred_lst]
pred_lst = sum(sum(pred_lst, []),[])
confusion_matrix(test_labels,pred_lst)

array([[33,  3],
       [ 3, 10]])

In [25]:
print(classification_report(test_labels,pred_lst))

              precision    recall  f1-score   support

           0       0.92      0.92      0.92        36
           1       0.77      0.77      0.77        13

    accuracy                           0.88        49
   macro avg       0.84      0.84      0.84        49
weighted avg       0.88      0.88      0.88        49



In [18]:
# torch.save(model, "bert_dense_model.pt")

In [ ]:
label_inf = []
inputs_inf = []
c = 0
with torch.no_grad():
    for k,v in data.items():
        if v["diag"] != "":
            try:
                label_inf.append(v["isRejection"])
#                 inputs_inf.append(get_cls_tensor(v["diag"],tokenizer, model))
            except e:
                print(e)
                
with open('inputs_inf.pkl', 'rb') as f:
    inputs_inf = pickle.load(f)

In [35]:
correct = 0
test_data = TensorDataset(train_features,torch.tensor(train_labels))
test_loader = DataLoader(test_data,
                          batch_size=BATCH_SIZE,shuffle=False)
loss = []
model.eval()
pred_lst = []
for x_test, y_test in test_loader:
    x_test, y_test = x_test.cuda(), y_test.cuda()
    output = model(x_test)

    pred = output.data.max(1, keepdim=True)[1]
    pred_lst.append(pred)
    correct += pred.eq(y_test.data.view_as(pred)).cuda().sum()
    #print(pred.eq(y_test.data.view_as(pred)).cuda(),pred.eq(y_test.data.view_as(pred)).cuda().sum())
print(correct)
print('Loss on test data is:{:.5f}'.format(np.mean(np.array(loss))))
print('Accuracy on test data is:{:.5f}%'.format(100.*correct / len(test_loader.dataset)))

tensor(141, device='cuda:0')
Loss on test data is:nan
Accuracy on test data is:73.05699%


/project/6049037/ytc1997/renal_nlp/lib/python3.7/site-packages/numpy/core/fromnumeric.py:3441: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/project/6049037/ytc1997/renal_nlp/lib/python3.7/site-packages/numpy/core/_methods.py:189: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


In [36]:
pred_lst = [x.tolist() for x in pred_lst]
pred_lst = sum(sum(pred_lst, []),[])
confusion_matrix(train_labels,pred_lst)

array([[121,  22],
       [ 30,  20]])

In [37]:
print(classification_report(train_labels,pred_lst))

              precision    recall  f1-score   support

           0       0.80      0.85      0.82       143
           1       0.48      0.40      0.43        50

    accuracy                           0.73       193
   macro avg       0.64      0.62      0.63       193
weighted avg       0.72      0.73      0.72       193



## Using List of Sentences Embedding and LSTM

In [69]:
max([len(x["pruned_report"]) for k,x in data.items()])

151

In [70]:
def get_cls_tensors(sents, tokenizer, model):
    tokenized_sents = tokenizer(sents,padding="max_length", truncation=True, return_tensors="pt",max_length=512)["input_ids"]
    last_hidden_state = model(tokenized_sents).last_hidden_state
    cls_state = last_hidden_state[:,0,:]
    zeros = torch.zeros(151-len(cls_state),768)
    result = torch.cat([cls_state,zeros])
    print(result.shape)
    return result


In [71]:
label = []
inputs_lstm = []
with torch.no_grad():
    for k,v in data.items():
        label.append(v["isRejection"])
        #inputs_lstm.append(get_cls_tensors(v["pruned_report"],tokenizer, model))
        
with open('inputs_lstm.pkl', 'rb') as f:
    inputs_lstm = pickle.load(f)

In [72]:
len(inputs_lstm)

242

In [73]:
train_features, test_features, train_labels, test_labels = train_test_split(inputs_lstm, label,random_state=1)

In [74]:
class SentLSTM(nn.Module):
  def __init__(self):
    super(SentLSTM,self).__init__()
    self.lstm = nn.LSTM(768,768)
    self.dropout = nn.Dropout(0.2)
    self.fc_layer = nn.Linear(768,2)
    self.softmax = nn.LogSoftmax()
    self.sigmoid = nn.Sigmoid()

  def forward(self,x):
    batch_size = x.size(1)

    output, self.hidden = self.lstm(x,self.hidden)
    #output = output.contiguous().view(-1, 128)
    #output = self.dropout(output[-1])
    output = output.permute(1,0,2).contiguous() #.view(batch_size,-1)
    #print(output.shape)
    output = self.fc_layer(output)
    #print(output.shape)
    output = torch.sum(output,1)
    #print(output.shape)
    output = self.softmax(output)
    #output = output.view(-1,batch_size,2)
    return output

  def init_hidden(self,size):
    return (torch.zeros(1, size, 768).cuda(), torch.zeros(1, size, 768).cuda())

In [75]:
def eval_accuracy(train_loader,model_name):
    total = 0
    correct2 = 0
    for i, (x_train, y_train) in enumerate(train_loader):

        x_train = x_train.swapaxes(0,1)
        x_train, y_train = x_train.cuda(), y_train.cuda()

        model_name.hidden = model_name.init_hidden(x_train.shape[1])
        output2 = model_name(x_train)

        pred2 = output2.data.max(1, keepdim=True)[1]
        correct2 += pred2.eq(y_train.data.view_as(pred2)).cuda().sum()
        total += len(y_train)
    return float(1.*correct2/total)

In [76]:
LR = 0.0001
iters = 0
BATCH_SIZE = 4
EPOCH = 100

train_data = TensorDataset(torch.stack(train_features),torch.tensor(train_labels))
train_loader = DataLoader(train_data,batch_size=BATCH_SIZE,shuffle=True)
test_data = TensorDataset(torch.stack(test_features),torch.tensor(test_labels))
test_loader = DataLoader(test_data, batch_size=BATCH_SIZE,shuffle=True)

In [77]:
for i, (x_train, y_train) in enumerate(train_loader):
    print(x_train.shape,x_train.swapaxes(0,1).shape,y_train)
    break

torch.Size([4, 151, 768]) torch.Size([151, 4, 768]) tensor([1, 0, 1, 0])


In [78]:


model = SentLSTM().cuda()
loss_nll = nn.NLLLoss().cuda()
optimizer = torch.optim.Adam(model.parameters(), lr=LR)


test_accuracy = []
train_accuracy = []

for e in range(EPOCH):
    for i, (x_train, y_train) in enumerate(train_loader):
        #x_train = x_train.view(-1, 1, 32, 32)  
        x_train = x_train.swapaxes(0,1)
        x_train, y_train = x_train.cuda(), y_train.cuda()
        model.train()
#         train_y = (i.label.cuda()-1) #.float()
#         train_x = torch.zeros(i.text.shape[0],i.text.shape[1],128).cuda()
#         for m in range(i.text.shape[0]):
#           train_x[m,range(i.text.shape[1]),i.text[m]] = 1

        model.hidden = model.init_hidden(x_train.shape[1])
        model.zero_grad()


        output = model(x_train)

        loss = loss_nll(output, y_train)                     
        loss.backward()                     
        optimizer.step()


    model.eval()
    print("epoch: {} step: {}/{} loss: {}".format(e,i*BATCH_SIZE,len(train_loader)*BATCH_SIZE,loss.item()))
    test_accuracy.append(eval_accuracy(train_loader,model))
    train_accuracy.append(eval_accuracy(test_loader,model))
    print("test accuracy now is: ",test_accuracy[-1])
    print("train accuracy now is: ",train_accuracy[-1])


/project/6049037/ytc1997/renal_nlp/lib/python3.7/site-packages/ipykernel_launcher.py:22: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.


epoch: 0 step: 180/184 loss: 2.980164051055908
test accuracy now is:  0.7569060921669006
train accuracy now is:  0.6885245442390442
epoch: 1 step: 180/184 loss: 0.3260575234889984
test accuracy now is:  0.7458564043045044
train accuracy now is:  0.6885245442390442
epoch: 2 step: 180/184 loss: 0.9650191068649292
test accuracy now is:  0.5580110549926758
train accuracy now is:  0.49180325865745544
epoch: 3 step: 180/184 loss: 0.19177201390266418
test accuracy now is:  0.7734807133674622
train accuracy now is:  0.7540982961654663
epoch: 4 step: 180/184 loss: 1.1096676588058472
test accuracy now is:  0.7569060921669006
train accuracy now is:  0.6885245442390442
epoch: 5 step: 180/184 loss: 1.393181324005127
test accuracy now is:  0.24309393763542175
train accuracy now is:  0.31147539615631104
epoch: 6 step: 180/184 loss: 2.8191065788269043
test accuracy now is:  0.7624309659004211
train accuracy now is:  0.6393442153930664
epoch: 7 step: 180/184 loss: 1.7102603912353516
test accuracy now i

In [25]:
original_sent = ["I eat apple","I like banana and apple","apple"]
tokenized_ori_sent = tokenizer(original_sent,padding="max_length", truncation=True, return_tensors="pt",max_length=512)["input_ids"]
ori_token_logits = model(tokenized_ori_sent)
ori_token_logits.last_hidden_state.shape

torch.Size([3, 512, 768])

In [6]:
with open('inputs_inf.pkl', 'wb') as f:
    pickle.dump(inputs_inf, f)

In [31]:
with open('inputs.pkl', 'rb') as f:
    b = pickle.load(f)

In [36]:
np.sum(label)

63

In [41]:
torch.mean(ori_token_logits.last_hidden_state[:,0,:],axis = 0)

tensor([ 4.9612e-01,  4.6588e-01, -5.6118e-01,  1.8390e-01, -9.7071e-02,
         1.9102e-02,  2.6681e-01, -2.2114e-02, -1.6363e-01, -7.8929e-02,
        -4.9337e-01,  1.1611e-01, -7.9099e-01,  3.1084e-01, -6.2471e-01,
         1.8267e-01,  1.9958e-01, -2.0421e-01, -8.2338e-02, -3.0284e-01,
        -1.0154e-02,  1.3414e-01, -2.0872e-01, -1.3390e-01, -3.5339e-01,
        -1.5284e-01,  8.8633e-01,  9.8529e-01, -3.1259e-01,  5.7725e-01,
        -3.7736e-01,  1.8224e-01,  1.2087e-01,  6.1886e-02, -4.8242e-01,
         6.8884e-01,  6.3927e-02,  1.3987e-01, -1.2440e-01, -6.3523e-02,
        -3.8300e-01,  1.2465e-01,  1.2864e+00,  4.9101e-01,  4.7505e-01,
        -8.1366e-01, -8.6218e-02,  5.7034e-02, -4.0028e-01,  5.5835e-01,
         1.0117e-01,  5.9038e-01,  4.1902e-01, -8.3233e-02,  3.9268e-01,
        -1.1761e-01, -9.5248e-01,  1.2101e-01, -1.1135e-01,  8.9056e-01,
         4.4104e-02,  3.9521e-01,  1.2744e-01, -2.2650e-01, -2.7314e-01,
        -8.8300e-02,  3.0635e-01,  1.4398e-01,  2.2

In [3]:
torch.stack([torch.tensor([1,2]),torch.tensor([3,4])])

tensor([[1, 2],
        [3, 4]])

In [3]:
original_sent = f"No organisms are seen on PAS, GMS or AFB stains, and there is no significant acute inflammation."
masked_sent = f"No organisms are seen on PAS, GMS or AFB stains, and there is no significant acute {tokenizer.mask_token}."
tokenized_sent = tokenizer.encode(masked_sent, return_tensors="pt")
mask_token_index = torch.where(tokenized_sent == tokenizer.mask_token_id)[1]


In [8]:
token_logits = model(tokenized_sent).logits
mask_token_logits = token_logits[0, mask_token_index, :]
top_5_tokens = torch.topk(mask_token_logits, 5, dim=1).indices[0].tolist()


In [9]:
for token in top_5_tokens:
    print(masked_sent.replace(tokenizer.mask_token,tokenizer.decode([token])))

No organisms are seen on PAS, GMS or AFB stains, and there is no significant acute change.
No organisms are seen on PAS, GMS or AFB stains, and there is no significant acute process.
No organisms are seen on PAS, GMS or AFB stains, and there is no significant acute infection.
No organisms are seen on PAS, GMS or AFB stains, and there is no significant acute changes.
No organisms are seen on PAS, GMS or AFB stains, and there is no significant acute decline.


In [32]:
tokenized_ori_sent = tokenizer.encode(original_sent, return_tensors="pt")
ori_token_logits = model(tokenized_ori_sent).logits
ori_token_logits

tensor([[[ -5.2346,  -6.2293,  -5.7876,  ...,  -6.2916,  -5.1632,  -6.1055],
         [ -9.7312, -14.2808,  -8.8388,  ...,  -8.6029, -10.1032, -11.5218],
         [ -3.2956,  -4.6892,   0.2737,  ...,  -2.1312,  -4.1391,  -1.8945],
         ...,
         [ -7.8746,  -7.5862,  -5.3626,  ...,  -6.7745,  -7.4311,  -6.2874],
         [-10.3461, -14.8237, -10.4709,  ..., -11.4858, -10.9951, -13.2184],
         [ -4.1543,  -5.3675,  -3.8452,  ...,  -5.4387,  -4.2856,  -5.8723]]],
       grad_fn=<AddBackward0>)

In [38]:
tokenized_ori_sent = tokenizer.encode(original_sent, return_tensors="pt")
ori_token_logits = model(tokenized_ori_sent)
len(ori_token_logits.last_hidden_state[0][0])

768

In [4]:
tokenized_sent

tensor([[  101,  1185, 12023,  1132,  1562,  1113,   185,  2225,   117,   176,
          4206,  1137,   170,  2087,  1830, 24754,  1116,   117,  1105,  1175,
          1110,  1185,  2418, 12104,   103,   119,   102]])

In [31]:
tokenizer.encode("No organisms are seen on", return_tensors="pt")

tensor([[  101,  1185, 12023,  1132,  1562,  1113,   102]])

In [30]:
tokenized_ori_sent

tensor([[  101,   178,  3940, 12075,   102],
        [  101,   178,  1176, 21806,   102]])

In [15]:
model(ex)

MaskedLMOutput(loss=None, logits=tensor([[[ -6.0741,  -6.0324,  -6.6350,  ...,  -6.3131,  -6.8833,  -7.4900],
         [ -8.1471,  -9.1584,  -8.7157,  ...,  -8.7917,  -8.8975,  -8.6561],
         [-11.9842, -11.3274, -10.2407,  ..., -10.0492, -10.1953, -12.9561],
         [ -9.4487,  -8.5138,  -7.9344,  ...,  -8.6140,  -8.8403,  -8.5834],
         [ -5.2699,  -5.0025,  -5.4685,  ...,  -8.0294,  -7.1379,  -6.7080]]],
       grad_fn=<AddBackward0>), hidden_states=None, attentions=None)

In [18]:
len(masked_sent.split())

17

In [17]:
masked_sent

'No organisms are seen on PAS, GMS or AFB stains, and there is no significant acute [MASK].'

In [23]:
tokenized_sent

tensor([[  101,  1185, 12023,  1132,  1562,  1113,   185,  2225,   117,   176,
          4206,  1137,   170,  2087,  1830, 24754,  1116,   117,  1105,  1175,
          1110,  1185,  2418, 12104,   103,   119,   102]])

In [28]:
mask_token_logits

tensor([[-4.9153, -6.2894, -3.6599,  ..., -4.9381, -5.6126, -5.2470]],
       grad_fn=<IndexBackward0>)